## Initialize

In [ ]:
%%capture
!pip install backtrader
!pip install mplfinance

In [35]:
import pandas as pd
from datetime import datetime
import os
import numpy as np
import time
import plotly.express as px
import shutil
import pandas as pd
import matplotlib.pyplot as plt


In [3]:
%%capture
from google.colab import drive
drive.mount('/content/gdrive', force_remount=True)

In [6]:

helper1 = "/content/gdrive/MyDrive/Algorithmic Trading System (ATS)/Code/helper.py"
helper2 = "/content/gdrive/MyDrive/Algorithmic Trading System (ATS)/Code/trade_list.py"
shutil.copy(helper1,  f'{os.getcwd() + "/" + "helper.py"}')
shutil.copy(helper2,  f'{os.getcwd() + "/" + "trade_list.py"}')

import trade_list
from helper import mlpplot, get_trade_list, get_indicators, get_summary_stats

## Load Data

In [12]:
# this file has the 1 min open high low close data for SPY for the last 1 year

spy_path = "/content/gdrive/MyDrive/Algorithmic Trading System (ATS)/Data/Historical/Raw/Stocks/SPY IB/SPY 1 min raw.csv"
spy_df = pd.read_csv(spy_path, parse_dates=True)
spy_df['date'] = pd.to_datetime(spy_df['date'])

In [17]:
# This folder has the 1 min ohlc data of SPY options for the last year for various strikes and expiry

folder_path = '/content/gdrive/MyDrive/Algorithmic Trading System (ATS)/Data/Historical/Raw/Options/SPY'  
file_names = os.listdir(folder_path)
print("There are a total of ", len(file_names), " options contracts data in this folder")
print("Every contract is named as follows ", file_names[0])

There are a total of  415  options contracts data in this folder
Every contract is named as follows  Options_raw_1min_Call_350.0_20230519.csv


In [18]:
# Load all the contracts data into a single dataframe 

expiry, strike, right, dfs, rows, min_date, max_date = [], [], [], [], [], [], []

for name in file_names:
    right.append(name.split("_")[3])
    strike.append(int(name.split("_")[4].split(".")[0]))
    expiry.append(name.split("_")[5].split(".")[0])
    df = pd.read_csv(folder_path + "/" + name)
    df['date'] = pd.to_datetime(df['date'])
    dfs.append(df)
    rows.append(df.shape[0])
    min_date.append(df['date'].min())
    max_date.append(df['date'].max())

Options = pd.DataFrame({"expiry" : expiry, "strike" : strike, "right" : right, "min_date" : min_date, "max_date" : max_date, "rows" : rows , "df" : dfs})

In [19]:
Options['time delta'] = Options['max_date'] - Options['min_date']
Options.sort_values(by = ['expiry', 'strike', 'right'], inplace= True)


In [22]:
# Each row is one contract and it looks as follows 
print("Row 1\n", Options.iloc[0], "\n")
print("The dataframe of ohlcv looks as follows\n:", Options['df'].iloc[0])

Row 1
 expiry                                                 20230519
strike                                                      350
right                                                      Call
min_date                                    2023-01-26 15:06:00
max_date                                    2023-05-18 16:14:00
rows                                                      16288
df                                 date   open   high    low...
time delta                                    112 days 01:08:00
Name: 0, dtype: object 

The dataframe of ohlcv looks as follows
:                      date   open   high    low  close  volume  average  \
0     2023-01-26 15:06:00  60.70  60.70  60.70  60.70    37.0    60.70   
1     2023-01-26 15:07:00  60.70  60.70  60.70  60.70     0.0    60.70   
2     2023-01-26 15:08:00  60.70  60.70  60.70  60.70     0.0    60.70   
3     2023-01-26 15:09:00  60.70  60.70  60.70  60.70     0.0    60.70   
4     2023-01-26 15:10:00  60.70  60.70  60.

## Calculate the Greeks
I found py_vollib works well and its easy to use

In [23]:
%%capture
!pip install py_vollib

In [24]:
import py_vollib.black_scholes.greeks.analytical as greeks
import py_vollib.black_scholes.implied_volatility as iv
from py_lets_be_rational.exceptions import BelowIntrinsicException


In [25]:
# I made these custom functions to calculate greeks for each row of the data

def calculate_option_greeks(option_type, spot_price, strike_price, time_to_expiry, risk_free_rate, implied_volatility):
    d1 = greeks.d1(spot_price, strike_price, time_to_expiry, risk_free_rate, implied_volatility)
    d2 = greeks.d2(spot_price, strike_price, time_to_expiry, risk_free_rate, implied_volatility)
    if option_type.lower() == 'call':
        delta = greeks.delta('c', spot_price, strike_price, time_to_expiry, risk_free_rate, implied_volatility)
        gamma = greeks.gamma('c', spot_price, strike_price, time_to_expiry, risk_free_rate, implied_volatility)
        theta = greeks.theta('c', spot_price, strike_price, time_to_expiry, risk_free_rate, implied_volatility)
        vega = greeks.vega('c', spot_price, strike_price, time_to_expiry, risk_free_rate, implied_volatility)
    elif option_type.lower() == 'put':
        delta = greeks.delta('p', spot_price, strike_price, time_to_expiry, risk_free_rate, implied_volatility)
        gamma = greeks.gamma('p', spot_price, strike_price, time_to_expiry, risk_free_rate, implied_volatility)
        theta = greeks.theta('p', spot_price, strike_price, time_to_expiry, risk_free_rate, implied_volatility)
        vega = greeks.vega('p', spot_price, strike_price, time_to_expiry, risk_free_rate, implied_volatility)
    else:
        raise ValueError("Invalid option type. Must be 'call' or 'put'.")

    return d1, d2, delta, gamma, theta, vega


In [26]:
def get_options_greeks(Options, expiry_date = "20230519", strike_price = 420, underlying = spy_df, underlying_name = "spy", risk_free_rate = 0.04):
    # Get the call and put contract data for the specified strike and strike
    df_call = Options[(Options['expiry'] == expiry_date) & (Options['strike'] == strike_price) & ((Options['right'] == "Call"))].iloc[0]["df"]
    df_put =  Options[(Options['expiry'] == expiry_date) & (Options['strike'] == strike_price) & ((Options['right'] == "Put"))].iloc[0]["df"]
    expiry_date = datetime.strptime(expiry_date + " - 16:00", '%Y%m%d - %H:%M')  

    # Convert to annualized time
    df_call['time_remaining'] = (expiry_date - df_call['date']).dt.total_seconds()  / (365 * 24 * 60 * 60)
    df_put['time_remaining'] = (expiry_date - df_put['date']).dt.total_seconds()  / (365 * 24 * 60 * 60)  

    # join underlying close prices 
    df_call = df_call.merge(underlying[['date', 'open', 'high', 'low', 'close']], on='date', how='left', suffixes=['', f'_{underlying_name}']).dropna()
    df_put = df_put.merge(underlying[['date', 'open', 'high', 'low', 'close']], on='date', how='left', suffixes=['', f'_{underlying_name}']).dropna()

    # Loop through each row and calculate the greeks 
    for index, row in df_call.iterrows():
        try:
            implied_volatility = iv.implied_volatility(row['close'], row['close_spy'], strike_price, row['time_remaining'], risk_free_rate, 'c')
        except BelowIntrinsicException:
            implied_volatility = 0.1

        df_call.loc[index, 'implied_volatility'] = implied_volatility
        d1, d2, delta, gamma, theta, vega = calculate_option_greeks('call', row['close_spy'], strike_price,
                                                                    row['time_remaining'],  risk_free_rate,
                                                                    implied_volatility)
        df_call.loc[index, 'delta'] = delta
        df_call.loc[index, 'gamma'] = gamma
        df_call.loc[index, 'theta'] = theta
        df_call.loc[index, 'vega'] = vega
        df_call.loc[index, 'd1'] = d1
        df_call.loc[index, 'd2'] = d2

    for index, row in df_put.iterrows():
        try:
            implied_volatility = iv.implied_volatility(row['close'], row['close_spy'], strike_price, row['time_remaining'], risk_free_rate, 'p')
        except BelowIntrinsicException:
            implied_volatility = 0.1

        df_put.loc[index, 'implied_volatility'] = implied_volatility
        d1, d2, delta, gamma, theta, vega = calculate_option_greeks('put', row['close_spy'], strike_price,
                                                                    row['time_remaining'],  risk_free_rate,
                                                                    implied_volatility)
        df_put.loc[index, 'delta'] = delta
        df_put.loc[index, 'gamma'] = gamma
        df_put.loc[index, 'theta'] = theta
        df_put.loc[index, 'vega'] = vega
        df_put.loc[index, 'd1'] = d1
        df_put.loc[index, 'd2'] = d2

    return df_call.reset_index(drop = True), df_put.reset_index(drop = True)



In [30]:
# get greeks for certain contract with the specified expiry and strike
 
df_call, df_put = get_options_greeks(Options, expiry_date = "20230519",
                                     strike_price = 420,
                                     underlying = spy_df,
                                     underlying_name = "spy",
                                     risk_free_rate = 0.04)

## Backest Using Backtrader

In [28]:
# Develop the strategy class 
import backtrader as bt
class DynamicDeltaHedging(bt.Strategy):
    params = (
        ('delta_check_interval', 60),  # Delta check interval in minutes
        ('multiplier', 100)
    )

    def __init__(self):
        self.call = self.datas[0]
        self.call_close = self.datas[0].close
        self.delta = self.datas[0].volume  # Delta values from df_call dataframe
        
        self.spy = self.datas[1]
        self.spy_close = self.datas[1].close  # Underlying data from df_spy dataframe
        self.delta_check_timer = self.params.delta_check_interval
        self.position_adjusted_first = False
        self.spy_position = 0


    def next(self):
        if not self.position_adjusted_first:
            # short the spy
            delta = self.delta[0]
            # print("initial delta is: ", delta)
            position = self.params.multiplier * delta
            self.order_target_size(data = self.spy, target=-int(position))

            # long the option 
            self.order_target_size(data = self.call, target = self.params.multiplier)

            self.position_adjusted_first = True
            self.spy_position = -int(position)

            # print("Spy initial position: ", self.spy_position)



        if self.delta_check_timer == 0:
            delta = self.delta[0]
            # print("new delta at loc: ", delta)  
            position = self.params.multiplier * delta + self.spy_position 
            # print("position changed by: ", -int(position))
            self.order_target_size(data=self.spy, target=-int(position))  

            self.spy_position = -int(position) + self.spy_position
            # print("new total spy_positon ", self.spy_position)
            self.delta_check_timer = self.params.delta_check_interval

        self.delta_check_timer -= 1


## Strategy Explained


1.   We want to start by taking a long position in the contract
2.   Next, we want to use the current delta and short certain number of underlyings (SPY)
3.   Further, we check our positions at every mintues interval and re-hedge our position if required. 
4.   For example, if the delta in the beginning was 0.10 and after 30 mins it is 0.11, we need to short one more SPY contract to achieve a dynamic hedge. 
5.   Else, if after 30 mins, the delta becomes 0.8, we need to buy 2 SPY contracts to hold only 8 SPY positions 




In [44]:
# Get ohlc data for trading
data_call = df_call[['date', 'open', 'high', 'low', 'close', 'delta']]
df_spy = df_call[['date', 'open_spy',	'high_spy',	'low_spy',	'close_spy']]

data_put = df_put[['date', 'open', 'high', 'low', 'close', 'delta']]
df_spy = df_put[['date', 'open_spy',	'high_spy',	'low_spy',	'close_spy']]

# set initial cash and commission value
cerebro = bt.Cerebro()
cerebro.broker.setcash(100000)
cerebro.broker.setcommission(commission=0)
# cerebro.broker.setcommission(commission=0.0005) 0.5% commission 

initial_value = cerebro.broker.getvalue()

data_call = bt.feeds.PandasData(dataname = data_call, datetime = 'date', open = 'open',
                               high = 'high', low = 'low', close = 'close', volume = 'delta')
cerebro.adddata(data_call)

# Create a DataFeed for underlying data
data_spy = bt.feeds.PandasData(dataname=df_spy, datetime='date', open = 'open_spy',
                               high = 'high_spy', low = 'low_spy', close = 'close_spy')
cerebro.adddata(data_spy)

cerebro.addstrategy(DynamicDeltaHedging, delta_check_interval=30)  # Set delta check interval to 60 minutes

# custom built analyser to get trade list
cerebro.addanalyzer(trade_list.trade_list, _name='trade_list')

# run backtest
results = cerebro.run(tradehistory=True)

# get results
df_trade = get_trade_list(results)


### Call Contract Prices

In [42]:
import plotly.graph_objects as go
fig = go.Figure(data=[go.Candlestick(x=df_call['date'],
                open=df_call['open'],
                high=df_call['high'],
                low=df_call['low'],
                close=df_call['close'])])
fig.show()

### Underlying prices 

In [43]:
fig = go.Figure(data=[go.Candlestick(x=df_call['date'],
                open=df_call['open_spy'],
                high=df_call['high_spy'],
                low=df_call['low_spy'],
                close=df_call['close_spy'])])
fig.show()

In [45]:
fig = px.line(df_trade, x="DateTimeOut", y="CummProfitLoss", title='Cummulative PNL')
fig.show()

**Conclusion**
By dynamically re-hedging we maintained our position as delta neutral and in no profit and no loss condition.

## Lets try hedging with Put contract - Strategy Explained


1.   We want to start by taking a long position in the contract
2.   Next, we want to use the current delta and short certain number of underlyings (SPY)
3.   Further, we check our positions at every mintues interval and re-hedge our position if required. 
4.   For example, if the delta in the beginning was 0.10 and after 30 mins it is 0.11, we need to short one more SPY contract to achieve a dynamic hedge. 
5.   Else, if after 30 mins, the delta becomes 0.8, we need to buy 2 SPY contracts to hold only 8 SPY positions 




In [46]:
# Get ohlc data for trading
data_call = df_call[['date', 'open', 'high', 'low', 'close', 'delta']]
df_spy = df_call[['date', 'open_spy',	'high_spy',	'low_spy',	'close_spy']]

data_put = df_put[['date', 'open', 'high', 'low', 'close', 'delta']]
df_spy = df_put[['date', 'open_spy',	'high_spy',	'low_spy',	'close_spy']]

# set initial cash and commission value
cerebro = bt.Cerebro()
cerebro.broker.setcash(100000)
cerebro.broker.setcommission(commission=0)
# cerebro.broker.setcommission(commission=0.0005) 0.5% commission 

initial_value = cerebro.broker.getvalue()

data_put = bt.feeds.PandasData(dataname = data_put, datetime = 'date', open = 'open',
                               high = 'high', low = 'low', close = 'close', volume = 'delta') # passing delta values as volume.
                                                                                              # we will edit it in the strategy class
cerebro.adddata(data_put)

# Create a DataFeed for underlying data
data_spy = bt.feeds.PandasData(dataname=df_spy, datetime='date', open = 'open_spy',
                               high = 'high_spy', low = 'low_spy', close = 'close_spy')
cerebro.adddata(data_spy)

cerebro.addstrategy(DynamicDeltaHedging, delta_check_interval=30)  # Set delta check interval to 60 minutes

# custom built analyser to get trade list
cerebro.addanalyzer(trade_list.trade_list, _name='trade_list')

# run backtest
results = cerebro.run(tradehistory=True)

# get results
df_trade = get_trade_list(results)


### Put Contract Data 

In [47]:
import plotly.graph_objects as go
fig = go.Figure(data=[go.Candlestick(x=df_put['date'],
                open=df_put['open'],
                high=df_put['high'],
                low=df_put['low'],
                close=df_put['close'])])
fig.show()

In [48]:
fig = px.line(df_trade, x="DateTimeOut", y="CummProfitLoss", title='Cummulative PNL')
fig.show()

**Conclusion**

As seen we can incur losses if we dont hedge frequently enough. If we change the check_interval to lower timeframes, we reduce the losses. But it would also lead to us make more trades and thereby more trade costs.

Also, adjust the commision to see how trade costs affect frequent re-hedging
